# EmbeddingLayer.py

In [2]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Mon Mar 20 23:41:51 2017

@author: red-sky
"""


import numpy as np
import theano
from theano import tensor as T


class EmbeddingLayer(object):
    def __init__(self, num_vocab, word_dim, rng, embedding_w=None):
        '''
        word_dim :: dimension of the word embeddings
        num_vocab :: number of word embeddings in the vocabulary
        embedding_w :: pre-train word vector
        '''

        if embedding_w is None:
            word_vectors = rng.uniform(-1.0, 1.0, (num_vocab, word_dim))
            self.embedding_w = theano.shared(word_vectors,
                                             name="EmbeddingLayer_W") \
                .astype(theano.config.floatX)
        else:
            self.embedding_w = theano.shared(embedding_w,
                                             name="EmbeddingLayer_W") \
                .astype(theano.config.floatX)

        self.params = [self.embedding_w]
        self.infor = [num_vocab, word_dim]

    def words_ind_2vec(self, index):
        map_word_vectors = self.embedding_w[index]
        output = T.mean(map_word_vectors,  axis=0)
        return output, map_word_vectors


if __name__ == "__main__":
    rng = np.random.RandomState(220495)
    arrWords = T.ivector("words")
    EMBD = EmbeddingLayer(100, 150, rng=rng)
    Word2Vec = theano.function(
        inputs=[arrWords],
        outputs=EMBD.words_ind_2vec(arrWords)
    )
    Vec = Word2Vec([1, 2, 3, 4])
    Vec = Word2Vec([2, 3, 4])
    print("Dim: ", Vec.shape)
    print("Val: ", Vec)

AttributeError: 'list' object has no attribute 'shape'

# EventEmbedding.py

In [3]:
import sys
import json
import theano
import pickle
import os.path
import numpy as np
import theano.tensor as T
from SmallUtils import createShareVar, ADAM_OPTIMIZER
from EmbeddingLayer import EmbeddingLayer
from RoleDependentLayer import RoleDependentLayer

更改過num_K: 150 -> 80

word_dim?? -> 100

更改all_index

修改ob1_real fake, act, obj2的datatype

In [8]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Sat Mar 25 17:36:33 2017

@author: red-sky
"""
import sys
import json
import theano
import pickle
import os.path
import numpy as np
import theano.tensor as T
from SmallUtils import createShareVar, ADAM_OPTIMIZER
from EmbeddingLayer import EmbeddingLayer
from RoleDependentLayer import RoleDependentLayer


class Input(object):
    def __init__(self, object1, object1_fake, action, object2, rng,
                 vovab_length=4000, wordDim=100, trainedWordsVectors=None,):
        # Init Embeding layer, input vector of index and ouput average
        # of word vector as ref Ding et al 2014
        self.EMBD = EmbeddingLayer(vovab_length, wordDim, rng=rng,
                                   embedding_w=trainedWordsVectors)

        object1_vector, _ = self.EMBD.words_ind_2vec(object1)
        action_vector, _ = self.EMBD.words_ind_2vec(action)
        object2_vector, _ = self.EMBD.words_ind_2vec(object2)
        object1_vector_fake, _ = self.EMBD.words_ind_2vec(object1_fake)

        self.output = [object1_vector, object1_vector_fake,
                       action_vector, object2_vector]
        self.params = self.EMBD.params

    def get_params(self):
        trainParams = {
            "WordWvec": self.EMBD.embedding_w.get_value()
        }
        return(trainParams)


class ModelBody(object):
    def __init__(self, vectorObjects, rng, n_out, n_in,
                 trainedModelParams=None):
        if trainedModelParams is None:
            trainedModelParams = {
                "roleDependentLayer1_": {
                    "T": None, "W1": None, "W2": None, "b": None
                },
                "roleDependentLayer2_": {
                    "T": None, "W1": None, "W2": None, "b": None
                },
                "roleDependentLayer3_": {
                    "T": None, "W1": None, "W2": None, "b": None
                }
            }

        Obj1, Ob1_fake, Act, Obj2 = vectorObjects
        
        ##
#         print(trainedModelParams["roleDependentLayer1_"]["T"].shape)
#         print(n_in, n_out)
        self.RoleDepen1 = RoleDependentLayer(
            left_dependent=T.stack([Obj1, Ob1_fake], axis=0),
            right_dependent=Act,
            n_in=n_in, n_out=n_out, rng=rng,
            trainedParams=trainedModelParams,
            name="roleDependentLayer1_"
        )
        self.RoleDepen1_output = self.RoleDepen1.output

        self.RoleDepen2 = RoleDependentLayer(
            left_dependent=Obj2,
            right_dependent=Act,
            n_in=n_in, n_out=n_out, rng=rng,
            trainedParams=trainedModelParams,
            name="roleDependentLayer2_"
        )
        self.RoleDepen2_output = T.flatten(self.RoleDepen2.output, outdim=1)

        self.RoleDepen3 = RoleDependentLayer(
            left_dependent=self.RoleDepen1_output,
            right_dependent=self.RoleDepen2_output,
            n_in=n_out, n_out=n_out, rng=rng,
            trainedParams=trainedModelParams,
            name="roleDependentLayer3_"
        )

        self.params = self.RoleDepen1.params + self.RoleDepen2.params + \
            self.RoleDepen3.params

        self.L2 = (
            self.RoleDepen1.L2 +
            self.RoleDepen2.L2 +
            self.RoleDepen3.L2
        )
        self.output = self.RoleDepen3.output

    def get_params(self):
        trainedModelParams = {
            "roleDependentLayer1_": self.RoleDepen1.get_params(),
            "roleDependentLayer2_": self.RoleDepen2.get_params(),
            "roleDependentLayer3_": self.RoleDepen3.get_params()
        }
        return(trainedModelParams)


class LogisticRegression(object):

    def __init__(self, rng, layerInput, n_in, n_out,
                 paramsLayer=None,
                 name="LogisticRegression_"):

        self.layerInput = layerInput
        if paramsLayer is None:
            self.W = createShareVar(rng=rng, name=name+"W",
                                    factor_for_init=n_out + n_in,
                                    dim=(n_in, n_out))
        else:
            self.W = theano.shared(value=paramsLayer["W"],
                                   name=name+"W", borrow=True)

        if paramsLayer is None:
            b_values = np.zeros((n_out,), dtype=theano.config.floatX)
            self.b = theano.shared(value=b_values,
                                   name=name+"b", borrow=True)
        else:
            self.b = theano.shared(value=paramsLayer["b"],
                                   name=name+"b", borrow=True)

        step1 = T.dot(self.layerInput, self.W)
        self.prob_givenX = T.tanh(step1 + self.b)
        self.y_predict = T.argmax(self.prob_givenX, axis=1)

        self.params = [self.W, self.b]
        self.L2 = sum([(param**2).sum() for param in self.params])

    def get_params(self):
        trainedParams = {
            "W": self.W.get_value(), "b": self.b.get_value()
        }
        return(trainedParams)

    def neg_log_likelihood(self, y_true):
        y_true = T.cast(y_true, "int32")
        log_prob = T.log(self.prob_givenX)
        nll = -T.mean(log_prob[T.arange(y_true.shape[0]), y_true])
        return nll

    def margin_loss(self):
        loss = T.max([0, 1 - self.prob_givenX[0, 0] + self.prob_givenX[1, 0]])
        return loss

    def cal_errors(self, y_true):
        if y_true.ndim != self.y_predict.ndim:
            raise TypeError(
                "y should have the same shape as self.y_pred",
                ("y_true", y_true.ndim, "y_pred", self.y_predict.ndim)
            )
        if y_true.dtype.startswith("int"):
            return T.mean(T.neq(self.y_predict, y_true))
        else:
            raise TypeError(
                "y_true should have type int ...",
                ("y_true", y_true.type, "y_pred", self.y_predict.type)
            )


# def main(dataPath, trainedParamsPath="modelTrained.pickle",
#          outputVectorPath="resultEmbeding.pickle",
#          learning_rate=0.005, L2_reg=0.0001,
#          n_epochs=500, num_K=150, word_dim=150):
def main(dataPath, trainedParamsPath="modelTrained.pickle",
         outputVectorPath="resultEmbeding.pickle",
         learning_rate=0.005, L2_reg=0.0001,
         n_epochs=500, num_K=80, word_dim=150):
    # CONSTANT VARIABLES
    RNG = np.random.RandomState(220495 + 280295 + 1)
    LABEL_NUM = 2
    if os.path.isfile(trainedParamsPath):
        with open(trainedParamsPath, 'rb') as handle:
            trainedParams = pickle.load(handle)
    else:
        print("No Trained Model, create new")
        I2V = np.load('./input/index2vector.npy')
        trainedParams = {
            "Input": {"WordWvec": I2V}, "Body": None, "Output": None
        }
#     print(trainedParams['Input']['WordWvec'])
    OPTIMIZER = ADAM_OPTIMIZER
    # INPUT DATA
    data_indexed_events = np.load(dataPath, allow_pickle=True)
    
    N_sample = len(data_indexed_events)
#    N_sample = 1
    all_index = []
    for i in data_indexed_events:
        for j in i:
            for k in j:
                all_index.append(k)
    all_index = list(set(all_index))
#     all_index = list(set(np.hstack(data_indexed_events.flat)))
#    all_train_index = list(set(np.hstack(data_indexed_events[0:NNN].flat)))
    # Snip tensor at begin
    object1 = T.ivector("object1")
    object1_fake = T.ivector("object1_fake")
    action = T.ivector("action")
    object2 = T.ivector("object2")

    constainY = theano.shared(
        np.asarray([1, 0], dtype=theano.config.floatX),
        borrow=True
    )

    # WORDS EMBEDING VECTOR
    wordsEmbedLayer = Input(
        object1=object1, object1_fake=object1_fake,
        action=action, object2=object2, rng=RNG,
        wordDim=word_dim, vovab_length=len(all_index),
        trainedWordsVectors=trainedParams["Input"]["WordWvec"]
    )
    
#     print(trainedParams['Input']['WordWvec'])
    Obj1, Ob1_fake, Act, Obj2 = wordsEmbedLayer.output

    # EVENTS EMBEDING LAYER - THREE ROLE DEPENTDENT LAYER
    eventsEmbedingLayer = ModelBody(
        vectorObjects=wordsEmbedLayer.output,
        n_out=num_K, n_in=word_dim, rng=RNG,
        trainedModelParams=trainedParams["Body"]
    )
    
#     print(trainedParams['Input']['WordWvec'])
    # CLASSIFY LAYER
    predict_layers = LogisticRegression(
        layerInput=eventsEmbedingLayer.output,
        rng=RNG, n_in=num_K, n_out=1,
        paramsLayer=trainedParams["Output"]
    )

    # COST FUNCTION
    COST = (
        predict_layers.margin_loss() +
        L2_reg * predict_layers.L2 +
        L2_reg * eventsEmbedingLayer.L2
    )

    # GRADIENT CALCULATION and UPDATE
    all_params = wordsEmbedLayer.params + \
        eventsEmbedingLayer.params + predict_layers.params
    print("TRAIN: ", all_params)

    UPDATE = OPTIMIZER(COST, all_params, learning_rate=learning_rate)

    # TRAIN MODEL
    GET_COST = theano.function(
        inputs=[object1, object1_fake, action, object2],
        outputs=[predict_layers.margin_loss(),
                 predict_layers.prob_givenX],
    )

#    TEST = theano.function(
#        inputs=[object1, object1_fake, action, object2],
#        outputs=eventsEmbedingLayer.RoleDepen2.test,
#        on_unused_input='warn'
#    )

    TRAIN = theano.function(
        inputs=[object1, object1_fake, action, object2],
        outputs=[predict_layers.margin_loss()],
        updates=UPDATE
    )

    GET_EVENT_VECTOR = theano.function(
        inputs=[object1, object1_fake, action, object2],
        outputs=[predict_layers.margin_loss(),
                 eventsEmbedingLayer.output],
    )

    def generate_fake_object(all_index, RNG, obj):
        fake_obj = list(RNG.choice(all_index, len(obj)))
        while sorted(fake_obj) == sorted(obj):
            print("WRONG faking object 1", obj)
            fake_obj = list(RNG.choice(all_index, len(obj)))
        return(fake_obj)

    def generate_list_object(data_indexed_events, all_index, RNG):
        list_fake_object1 = [
            generate_fake_object(all_index, RNG, events[0])
            for events in data_indexed_events
        ]
        list_real_object = set([
            "_".join([str(a) for a in sorted(events[0])])
            for events in data_indexed_events
        ])
        wrong = 0
        while True:
            valid = True
            wrong += 1
            for i, obj in enumerate(list_fake_object1):
                s = "_".join([str(a) for a in sorted(obj)])
                if s in list_real_object:
                    valid = valid and False
                    list_fake_object1[i] = \
                        generate_fake_object(all_index, RNG, s)
                else:
                    valid = valid and True
            if valid:
                break
        print("There are %d wrong random loops" % wrong)
        return(list_fake_object1)

    print("*"*72)
    print("Begin Training process")

    for epoch in range(n_epochs):
        # create false label
        print("Begin new epoch: %d" % epoch)

        list_fake_object1 = generate_list_object(data_indexed_events,
                                                 all_index, RNG)
        cost_of_epoch = []
        set_index = set(range(N_sample))
        temp_variable = N_sample
        print("*" * 72+"\n")
        print("*" * 72+"\n")
        # train
        model_train = {
            "Input": wordsEmbedLayer.get_params(),
            "Body": eventsEmbedingLayer.get_params(),
            "Output": predict_layers.get_params()
        }
        RESULT = {}
        outCOST = []
        Max_inter = len(set_index)*2
        iter_num = 0
        while len(set_index) > 0 and iter_num <= Max_inter:
            iter_num += 1
            index = set_index.pop()
            ob1_real, act, obj2 = data_indexed_events[index]
            ob1_fake = list_fake_object1[index]
            
            ob1_real = np.array(ob1_real, dtype=np.int32)
            ob1_fake = np.array(ob1_fake, dtype=np.int32)
            act = np.array(act, dtype=np.int32)
            obj2 = np.array(obj2, dtype=np.int32)

            cost, probY = GET_COST(ob1_real, ob1_fake, act, obj2)
            outCOST.append(cost)
#            test = TEST(ob1_real, ob1_fake, act, obj2)
#            for a in test:
#                print(a, a.shape)

            if cost > 0:
                set_index.add(index)
                c = TRAIN(ob1_real, ob1_fake, act, obj2)
            else:
                RESULT[index] = GET_EVENT_VECTOR(ob1_real, ob1_fake, act, obj2)

            if (len(set_index) % 50 == 0 and
                    temp_variable != len(set_index)):
                temp_variable = len(set_index)
                print("There are %f %% left in this %d "
                      "epoch with average cost %f"
                      % (len(set_index)/float(N_sample)*100,
                         epoch, np.mean(outCOST[-50:])))
#             if iter_num > Max_inter - 5:
#                 print(set_index, ob1_real, ob1_fake, act, obj2)

        with open(trainedParamsPath, 'wb') as handle:
            pickle.dump(model_train, handle,
                        protocol=pickle.HIGHEST_PROTOCOL)

        with open(outputVectorPath, 'wb') as handle:
            pickle.dump(RESULT, handle,
                        protocol=pickle.HIGHEST_PROTOCOL)

if __name__ == "__main__":
#     arg = ["", "Data/Query_Apple/2005-2010/IndexedEvents.npy",
#           "Data/Query_Apple/2005-2010/linhtinh/", "20"]
#     arg = sys.argv
    arg = ["", "/Users/arthur/Desktop/OpenIEStanza_EventEmbedding/input/event2index.npy",
          "/Users/arthur/Desktop/OpenIEStanza_EventEmbedding/input/", "1"]
    main(dataPath=arg[1], trainedParamsPath=arg[2]+"TrainedParams.pickle",
         outputVectorPath=arg[2]+"resultEmbeding.pickle", n_epochs=int(arg[3]), word_dim=100)

No Trained Model, create new
[[-0.01028071  0.00297011  0.08961353 ... -0.12963143  0.01607524
   0.11525529]
 [-0.13910691  0.11187849  0.10047291 ... -0.07176132 -0.19421659
   0.01534512]
 [ 0.00135416  0.0544313  -0.11973946 ...  0.00895901  0.1445961
  -0.12278345]
 ...
 [-0.01154993 -0.00363348 -0.0078348  ... -0.15638947 -0.05968169
  -0.05379232]
 [-0.1383462   0.1326232  -0.09315939 ... -0.10181806  0.01006989
   0.04388671]
 [-0.10029647  0.17595828  0.01288539 ...  0.01475195  0.13340817
  -0.0461543 ]]
[[-0.01028071  0.00297011  0.08961353 ... -0.12963143  0.01607524
   0.11525529]
 [-0.13910691  0.11187849  0.10047291 ... -0.07176132 -0.19421659
   0.01534512]
 [ 0.00135416  0.0544313  -0.11973946 ...  0.00895901  0.1445961
  -0.12278345]
 ...
 [-0.01154993 -0.00363348 -0.0078348  ... -0.15638947 -0.05968169
  -0.05379232]
 [-0.1383462   0.1326232  -0.09315939 ... -0.10181806  0.01006989
   0.04388671]
 [-0.10029647  0.17595828  0.01288539 ...  0.01475195  0.13340817
  -0.

/opt/anaconda3/lib/python3.9/site-packages/theano/tensor/basic.py:5280: UserWarning: flatten outdim parameter is deprecated, use ndim instead.
  warnings.warn(


************************************************************************
Begin Training process
Begin new epoch: 0
WRONG faking object 1 [83]
WRONG faking object 1 [1534]
WRONG faking object 1 [20193]
WRONG faking object 1 [220]
WRONG faking object 1 [445]
WRONG faking object 1 [5297]
WRONG faking object 1 [1165]
There are 3 wrong random loops
************************************************************************

************************************************************************

There are 99.986836 % left in this 0 epoch with average cost 0.793423
There are 99.956918 % left in this 0 epoch with average cost 0.776141
There are 99.926999 % left in this 0 epoch with average cost 0.709594
There are 99.897081 % left in this 0 epoch with average cost 0.640615
There are 99.867163 % left in this 0 epoch with average cost 0.828629
There are 99.837245 % left in this 0 epoch with average cost 0.837082
There are 99.807326 % left in this 0 epoch with average cost 0.602430
There are 99.777

There are 96.695827 % left in this 0 epoch with average cost 0.588982
There are 96.665909 % left in this 0 epoch with average cost 0.694210
There are 96.635990 % left in this 0 epoch with average cost 0.654107
There are 96.606072 % left in this 0 epoch with average cost 0.526574
There are 96.576154 % left in this 0 epoch with average cost 0.554615
There are 96.546236 % left in this 0 epoch with average cost 0.582129
There are 96.516317 % left in this 0 epoch with average cost 0.817837
There are 96.486399 % left in this 0 epoch with average cost 0.889625
There are 96.456481 % left in this 0 epoch with average cost 0.549719
There are 96.426563 % left in this 0 epoch with average cost 0.597838
There are 96.396644 % left in this 0 epoch with average cost 0.650917
There are 96.366726 % left in this 0 epoch with average cost 0.723581
There are 96.336808 % left in this 0 epoch with average cost 0.653588
There are 96.306890 % left in this 0 epoch with average cost 0.648486
There are 96.276971 

There are 93.165472 % left in this 0 epoch with average cost 0.568916
There are 93.135554 % left in this 0 epoch with average cost 0.796719
There are 93.105635 % left in this 0 epoch with average cost 0.592638
There are 93.075717 % left in this 0 epoch with average cost 0.374481
There are 93.045799 % left in this 0 epoch with average cost 0.529296
There are 93.015881 % left in this 0 epoch with average cost 0.369710
There are 92.985962 % left in this 0 epoch with average cost 0.461411
There are 92.956044 % left in this 0 epoch with average cost 0.633742
There are 92.926126 % left in this 0 epoch with average cost 0.708157
There are 92.896208 % left in this 0 epoch with average cost 0.762821
There are 92.866289 % left in this 0 epoch with average cost 0.532338
There are 92.836371 % left in this 0 epoch with average cost 0.688129
There are 92.806453 % left in this 0 epoch with average cost 0.661338
There are 92.776535 % left in this 0 epoch with average cost 0.572313
There are 92.746616 

...

{104207, 5, 10, 18, 24, 25, 104211, 104215, 47, 60, 62, 72, 120875, 104221, 77, 104222, 118791, 72945, 90, 99, 104226, 102, 103, 105, 107, 111, 112, 114, 118, 120, 104230, 125, 104231, 104233, 137, 142, 144, 104235, 104236, 154, 155, 104237, 158, 164, 72948, 170, 104240, 104241, 179, 104242, 72949, 190, 191, 192, 104244, 104245, 200, 201, 104246, 206, 207, 208, 118792, 104248, 214, 72950, 104250, 104252, 232, 104253, 240, 241, 242, 104254, 246, 247, 249, 104256, 252, 254, 256, 257, 259, 104258, 72952, 265, 104259, 278, 283, 284, 104264, 299, 304, 104267, 104270, 104271, 330, 104274, 344, 347, 352, 354, 355, 104277, 359, 361, 104278, 364, 365, 104279, 72956, 371, 104280, 375, 381, 104282, 384, 386, 391, 392, 397, 398, 400, 104286, 414, 72958, 104290, 423, 424, 427, 104291, 432, 435, 436, 442, 452, 453, 456, 457, 458, 104298, 104299, 72960, 472, 104300, 475, 480, 481, 104302, 485, 487, 492, 104304, 495, 498, 500, 104306, 104307, 104308, 517, 518, 72962, 526, 104311, 531, 533, 104313, 539

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Begin new epoch: 2
WRONG faking object 1 [4922]
WRONG faking object 1 [11189]
WRONG faking object 1 [105]
WRONG faking object 1 [7708]
WRONG faking object 1 [6]
WRONG faking object 1 [320]
WRONG faking object 1 [1027]
WRONG faking object 1 [157]
WRONG faking object 1 [4658]
WRONG faking object 1 [801]
There are 3 wrong random loops
************************************************************************

************************************************************************

There are 99.986836 % left in this 2 epoch with average cost 0.958746
There are 99.956918 % left in this 2 epoch with average cost 0.946296
There are 99.926999 % left in this 2 epoch with average cost 1.041976
There are 99.897081 % left in this 2 epoch with average cost 0.959696
There are 99.867163 % left in this 2 epoch with average cost 0.937901
There are 99.837245 % left in this 2 epoch with average cost 0.908410
There are 99.807326 % left in this 2 epoch with average cost 1.016279
There are 99.777408 % left i

There are 96.665909 % left in this 2 epoch with average cost 0.939205
There are 96.635990 % left in this 2 epoch with average cost 0.979342
There are 96.606072 % left in this 2 epoch with average cost 0.863897
There are 96.576154 % left in this 2 epoch with average cost 0.934755
There are 96.546236 % left in this 2 epoch with average cost 0.981610
There are 96.516317 % left in this 2 epoch with average cost 1.032192
There are 96.486399 % left in this 2 epoch with average cost 1.030816
There are 96.456481 % left in this 2 epoch with average cost 0.878521
There are 96.426563 % left in this 2 epoch with average cost 0.763525
There are 96.396644 % left in this 2 epoch with average cost 0.929817
There are 96.366726 % left in this 2 epoch with average cost 1.045717
There are 96.336808 % left in this 2 epoch with average cost 0.974189
There are 96.306890 % left in this 2 epoch with average cost 0.893356
There are 96.276971 % left in this 2 epoch with average cost 1.021295
There are 96.247053 

KeyboardInterrupt: 

In [73]:
test2 = np.load('/Users/arthur/Desktop/OpenIEStanza_EventEmbedding/input/event2index.npy', allow_pickle=True)

# RoleDependentLayer.py

In [4]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Sat Mar 25 16:13:18 2017

@author: red-sky
"""

import theano
import numpy as np
import theano.tensor as T
from SmallUtils import createShareVar


class RoleDependentLayer(object):
    def __init__(self, left_dependent, right_dependent, rng,
                 n_in=100, n_out=4, trainedParams=None,
                 name="RoleDependentEmbedding_"):
        if trainedParams is None:
            trainedParams = {
                name: {
                    "T": None, "W1": None, "W2": None, "b": None
                }
            }
#        print(name)
        if trainedParams[name]["T"] is not None:
#            print(trainedParams[name]["T"])
#            print(trainedParams[name]["T"].shape)
#            print(n_out, n_in, n_in)
            assert trainedParams[name]["T"].shape == (n_out, n_in, n_in)
            self.T = theano.shared(value=trainedParams[name]["T"],
                                   name=name+"T", borrow=True)
        else:
            self.T = createShareVar(rng=rng, name=name+"T",
                                    factor_for_init=n_out + n_in,
                                    dim=(n_out, n_in, n_in))

        if trainedParams[name]["W1"] is not None:
            assert trainedParams[name]["W1"].shape == (n_in, n_out)
            self.W1 = theano.shared(value=trainedParams[name]["W1"],
                                    name=name+"W1", borrow=True)
        else:
            self.W1 = createShareVar(rng=rng, name=name+"W1",
                                     factor_for_init=n_out + n_in,
                                     dim=(n_in, n_out))

        if trainedParams[name]["W2"] is not None:
            assert trainedParams[name]["W2"].shape == (n_in, n_out)
            self.W2 = theano.shared(value=trainedParams[name]["W2"],
                                    name=name+"W2", borrow=True)
        else:
            self.W2 = createShareVar(rng=rng, name=name+"W2",
                                     factor_for_init=n_out + n_in,
                                     dim=(n_in, n_out))

        if trainedParams[name]["b"] is not None:
            assert trainedParams[name]["b"].shape == (n_out,)
            self.b = theano.shared(value=trainedParams[name]["b"],
                                   name=name+"b", borrow=True)
        else:
            b_values = np.zeros(shape=(n_out,), dtype=theano.config.floatX)
            self.b = theano.shared(value=b_values, name=name+"b", borrow=True)

        # list of layer params
        self.params = [self.T, self.W1, self.W2, self.b]

        # L2 regulation
        self.L2 = sum([(param**2).sum() for param in self.params])

        # Bi-linear step
        def one_kernel(Tk, left, right):
            first_bi_libear = theano.dot(left, Tk)
            seccon_bi_linear = theano.dot(first_bi_libear, right)
            return(seccon_bi_linear.flatten())

        bi_1, _ = theano.scan(
            fn=one_kernel,
            sequences=[self.T],
            non_sequences=[left_dependent, right_dependent],
            n_steps=n_out
        )

        # Feed forward network step
        feedforward_step1 = theano.dot(left_dependent, self.W1)
        feedforward_step2 = theano.dot(right_dependent, self.W2)
        feedforward_step3 = (feedforward_step1 +
                             feedforward_step2.dimshuffle("x", 0) +
                             self.b.dimshuffle("x", 0))
        feedforward_step4 = bi_1.dimshuffle(1, 0) + feedforward_step3
        self.output = theano.tensor.tanh(feedforward_step4)
        self.test = [feedforward_step3]

    def output_(self, left_dependent, right_dependent):

        def one_kernel(Tk, left, right):
            first_bi_libear = theano.dot(left, Tk)
            seccon_bi_linear = theano.dot(first_bi_libear, right)
            return(seccon_bi_linear.flatten())

        bi_linear_tensor, _ = theano.scan(
            fn=one_kernel,
            sequences=[self.T],
            non_sequences=[left_dependent, right_dependent],
            n_steps=n_out
        )

        bi_linear_tensor = bi_linear_tensor.dimshuffle(1, 0)
        feedforward_step1 = theano.dot(left_dependent, self.W1)
        feedforward_step2 = theano.dot(right_dependent, self.W2)
        feedforward_step3 = (feedforward_step1 +
                             feedforward_step2.dimshuffle("x", 0) +
                             self.b.dimshuffle("x", 0))
        feedforward_step4 = bi_linear_tensor + feedforward_step3
        output = theano.tensor.tanh(feedforward_step4)
        return(output)

    def get_params(self):
        trainedParams = {
            "T": self.T.get_value(), "W1": self.W1.get_value(),
            "W2": self.W2.get_value(), "b": self.b.get_value()
        }
        return(trainedParams)

# SmallUtils.py

In [5]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Sat Mar 25 15:55:14 2017

@author: red-sky
"""
import theano
import theano.tensor as T
import numpy as np

def createShareVar(rng, dim, name, factor_for_init):
    var_values = np.asarray(
        rng.uniform(
            low=-np.sqrt(6.0 / factor_for_init),
            high=np.sqrt(6.0 / factor_for_init),
            size=dim,
        )
    )
    Var = theano.shared(value=var_values, name=name, borrow=True)
    return Var


def adadelta(lr, tparams, cost, grads, listInput):
    """
    An adaptive learning rate optimizer

    Parameters
    ----------
    lr : Theano SharedVariable
        Initial learning rate
    tpramas: Theano SharedVariable
        Model parameters
    grads: Theano variable
        Gradients of cost w.r.t to parameres

    cost: Theano variable
        Objective fucntion to minimize

    Notes
    -----
    For more information, see [ADADELTA]_.

    .. [ADADELTA] Matthew D. Zeiler, *ADADELTA: An Adaptive Learning
       Rate Method*, arXiv:1212.5701.
    """
    np_float = np.asarray(0., dtype=theano.config.floatX)
    zipped_grads = [theano.shared(p.get_value() * np_float,
                                  name='%s_grad' % k)
                    for k, p in enumerate(tparams)]
    running_up2 = [theano.shared(p.get_value() * np_float,
                                 name='%s_rup2' % k)
                   for k, p in enumerate(tparams)]
    running_grads2 = [theano.shared(p.get_value() * np_float,
                                    name='%s_rgrad2' % k)
                      for k, p in enumerate(tparams)]

    zgup = [(zg, g) for zg, g in zip(zipped_grads, grads)]
    rg2up = [(rg2, 0.95 * rg2 + 0.05 * (g ** 2))
             for rg2, g in zip(running_grads2, grads)]

    f_grad_shared = theano.function(inputs=listInput,
                                    outputs=cost,
                                    updates=zgup + rg2up,
                                    name='adadelta_f_grad_shared')

    updir = [-T.sqrt(ru2 + 1e-6) / T.sqrt(rg2 + 1e-6) * zg
             for zg, ru2, rg2 in zip(zipped_grads,
                                     running_up2,
                                     running_grads2)]
    ru2up = [(ru2, 0.95 * ru2 + 0.05 * (ud ** 2))
             for ru2, ud in zip(running_up2, updir)]
    param_up = [(p, p + ud) for p, ud in zip(tparams, updir)]

    f_update = theano.function([lr], [], updates=ru2up + param_up,
                               on_unused_input='ignore',
                               name='adadelta_f_update')

    return f_grad_shared, f_update


def ADAM_OPTIMIZER(loss, all_params, learning_rate=0.001,
                   b1=0.9, b2=0.999, e=1e-8, gamma=1-1e-8):
    """
    CITE: http://sebastianruder.com/optimizing-gradient-descent/index.html#adam
    ADAM update rules
    Default values are taken from [Kingma2014]
    References:
    [Kingma2014] Kingma, Diederik, and Jimmy Ba.
    "Adam: A Method for Stochastic Optimization."
    arXiv preprint arXiv:1412.6980 (2014).
    http://arxiv.org/pdf/1412.6980v4.pdf
    """
    updates = []
    all_grads = theano.grad(loss, all_params)
    alpha = learning_rate
    t = theano.shared(np.float32(1))
    # (Decay the first moment running average coefficient)
    b1_t = b1*gamma**(t-1)

    for params_previous, g in zip(all_params, all_grads):
        init_moment = np.zeros(params_previous.get_value().shape,
                               dtype=theano.config.floatX)
        # (the mean)
        first_moment = theano.shared(init_moment)
        # (the uncentered variance)
        second_moment = theano.shared(init_moment)

        # (Update biased first moment estimate)
        bias_m = b1_t*first_moment + (1 - b1_t)*g

        # (Update biased second raw moment estimate)
        bias_v = b2*second_moment + (1 - b2)*g**2

        # (Compute bias-corrected first moment estimate)
        unbias_m = bias_m / (1-b1**t)

        # (Compute bias-corrected second raw moment estimate)
        unbias_v = bias_v / (1-b2**t)

        # (Update parameters)
        update_term = (alpha * unbias_m) / (T.sqrt(unbias_v) + e)
        params_new = params_previous - update_term

        updates.append((first_moment, bias_m))
        updates.append((second_moment, bias_v))
        updates.append((params_previous, params_new))
    updates.append((t, t + 1.))
    return updates


## 下面不用了

In [23]:
import os
import numpy as np
import torch
from torch import nn
from torch.utils.data import DataLoader
from torchvision import datasets, transforms
from torchvision.transforms import ToTensor, Lambda
# pip install torchvision

In [5]:
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using {device} device")

Using cpu device


In [37]:
class NeuralNetwork(nn.Module):
    def __init__(self):
        super(NeuralNetwork, self).__init__()
        self.flatten = nn.Flatten()
        self.linear_relu_stack = nn.Sequential(
            nn.Linear(28*28, 512),
            nn.ReLU(),
            nn.Linear(512, 512),
            nn.ReLU(),
            nn.Linear(512, 10),
        )

    def forward(self, x):
        x = self.flatten(x)
        logits = self.linear_relu_stack(x)
        return logits
model = NeuralNetwork().to(device)
print(model)

NeuralNetwork(
  (flatten): Flatten(start_dim=1, end_dim=-1)
  (linear_relu_stack): Sequential(
    (0): Linear(in_features=784, out_features=512, bias=True)
    (1): ReLU()
    (2): Linear(in_features=512, out_features=512, bias=True)
    (3): ReLU()
    (4): Linear(in_features=512, out_features=10, bias=True)
  )
)


In [ ]:
class NeuralNetwork(nn.Module):
    def __init__(self):
        super(NeuralNetwork, self).__init__()
        self.flatten = nn.Flatten()
        self.linear_relu_stack = nn.Sequential(
            nn.Linear(28*28, 512),
            nn.ReLU(),
            nn.Linear(512, 512),
            nn.ReLU(),
            nn.Linear(512, 10),
        )

    def forward(self, x):
        x = self.flatten(x)
        logits = self.linear_relu_stack(x)
        return logits

model = NeuralNetwork()

In [8]:
X = torch.rand(1, 28, 28, device=device)
logits = model(X)
pred_probab = nn.Softmax(dim=1)(logits)
y_pred = pred_probab.argmax(1)
print(f"Predicted class: {y_pred}")

Predicted class: tensor([2])


In [13]:
X
X[0, 0, 1]

tensor(0.9494)

In [19]:
#1
input_image = torch.rand(3,28,28)
print(input_image.size())

#2
flatten = nn.Flatten()
flat_image = flatten(input_image)
print(flat_image.size())

#3
layer1 = nn.Linear(in_features=28*28, out_features=20)
hidden1 = layer1(flat_image)
print(hidden1.size())

#4
print(f"Before ReLU: {hidden1}\n\n")
hidden1 = nn.ReLU()(hidden1)
print(f"After ReLU: {hidden1}")

#5
seq_modules = nn.Sequential(
    flatten,
    layer1,
    nn.ReLU(),
    nn.Linear(20, 10)
)
input_image = torch.rand(3,28,28)
logits = seq_modules(input_image)

#6
softmax = nn.Softmax(dim=1)
pred_probab = softmax(logits)
print(pred_probab)

#7
print(f"Model structure: {model}\n\n")

for name, param in model.named_parameters():
    print(f"Layer: {name} | Size: {param.size()} | Values : {param[:2]} \n")

torch.Size([3, 28, 28])
torch.Size([3, 784])
torch.Size([3, 20])
Before ReLU: tensor([[ 0.0305, -0.5532,  0.7130,  0.8898,  0.0230, -0.2422, -0.2477, -0.2424,
         -0.0642, -0.1797,  0.2153,  0.0757,  0.2777,  0.0609,  0.1148, -0.9117,
          0.3570, -0.4060,  0.4346,  0.3369],
        [ 0.1104, -0.2133,  0.6152,  0.4745, -0.0112,  0.0866, -0.3030, -0.4700,
          0.0877, -0.2403,  0.0436,  0.0757,  0.0117, -0.0613, -0.1673, -0.9643,
          0.4333, -0.3328,  0.6907,  0.1493],
        [ 0.0368, -0.3006,  0.8761,  0.7100,  0.0723,  0.3564, -0.4708, -0.2543,
         -0.0399, -0.2391,  0.0966,  0.3240,  0.1662,  0.2291, -0.1094, -0.9933,
          0.5804, -0.2566,  0.5009,  0.3386]], grad_fn=<AddmmBackward0>)


After ReLU: tensor([[0.0305, 0.0000, 0.7130, 0.8898, 0.0230, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.2153, 0.0757, 0.2777, 0.0609, 0.1148, 0.0000, 0.3570, 0.0000,
         0.4346, 0.3369],
        [0.1104, 0.0000, 0.6152, 0.4745, 0.0000, 0.0866, 0.0000, 0.00

In [28]:
torch.tensor(np.array([2, 1]))

tensor([2, 1])

In [29]:
O1 = torch.rand(50,100,1)
P = torch.rand(50,100,1)
O2 = torch.rand(50,100,1)

In [38]:
pwd

'/Users/arthur/Desktop/OpenIEStanza_EventEmbedding'